# A Socio-Economic Model of Segregation, Neighborhood Change and Housing Inequality
## Part I: Agent-based Model and Computational Experiments
### Malte Grönemann

I formalize the theoretical argument presented in the paper using an agent-based model, where agents interact on a regular spatial grid, as popularized by Schelling (1971). The model is primarily based on the model by Benard and Willer (2007). There are two classes of agents that interact with each other and themselves. Households occupy housing units and want to live in those housing units that maximize their residential satisfaction, i.e. utility, which is a function of housing quality and neighborhood status, given their budget. They are mobile, so they can move in and out of housing units and neighborhoods if there are vacant units. Landlords own the housing units, which are represented by the cells on the city grid. They need to decide whether it is profitable to invest in their housing units, which they do heuristically based on changes in rents in the neighborhood.

The following sections describe the model and the computational experiments. It also provides a single-run animation to foster understanding and gives you the opportunity to play around with parameters of the model. The computational experiments are conducted using separate files without the explanations and the animation.

In [7]:
import agentpy as ap
import numpy as np
import pandas as pd
import random

import matplotlib.pyplot as plt
import IPython

## Defining Agents

### Households

Households are the demanders of housing. Each household $i$ is characterised by their income disposable on housing $w_i \in [0, 1]$ and their social status $s_i \in [0, 1]$. Both household attributes are fixed over time. Income distributions are almost always positively skewed and long-tailed. I sample the household's income from a $Beta(2, \ 5)$ distribution to capture this typical feature while cutting down on model sophistication. Income inequality in samples from this distribution, as measured by the Gini index, averages about 31.5, which is comparable to the level of income inequality in Germany, France, and Canada in recent years.  I assume a similar distributional form for social status $s_i$, which is typically correlated with income. The social status is therefore sampled dependent on income and a correlation parameter $r \in [0, 1]$:

$$ s_i \sim r \ w_i \\ + \\ (1 - r) \ Beta(2, \ 5) $$

Housing in this model represents a consumption bundle $x$ of two commodities, housing quality $q(x, t)$ and neighborhood status $\bar{s}(x, t)$, which are variable over time $t$. Housing quality is variable because landlords can invest (see section on supply), and neighborhood status is variable over time as households can move into and out of units and neighborhoods. Housing quality represents the desirability of the unit, while neighborhood status represents the desirability of the neighborhood. I operationalize neighborhood status as the average social status of the inhabitants $j$ of the housing units in the Moore neighborhood of the housing unit $x$ that household $i$ considers moving to at time $t$. $n_{x, t}$ is the number of neighbors the household would have at that location, i.e., the number of occupied housing units neighboring $x$ at time $t$. The social position of a neighbor $j$ at location $x$ at time $t$ is referred to by $s_{j}(x, t)$.

$$ \bar{s}(x, t) = \frac{1}{n_{j}(x, t)} \sum_{j = 1}^{n_{j}(x, t)} s_{j} $$

I propose the following Cobb-Douglas utility function to model the household's housing preferences. The parameter $a \in [0, 1]$ weighs the two commodities and expresses how important social preferences are relative to housing quality. If $a = 0$, only housing quality matters in the utility calculation of the household; at $a = 1$, only average social status matters. $a$ is identical for all households in a given simulation run, therefore, all housing units are equally desirable to all households.

$$ U(x, t) = \\ \bar{s}(x, t)^a \\ q(x, t)^{1-a} $$

The set of all housing units $x$ at time $t$ is denoted by $X(t)$, and the set of renters inhabiting housing unit $x$ at time $t$ is denoted $L(x, t)$, which can contain at most one renter: $|L(x, t)| \leq 1 \ \forall \ x, t$. For each household $i$, there is a set of available options, the *budget set* $B_i(t) \subseteq X(t)$. The housing units in this set are the household's current and unoccupied locations if the rent $p(x, t)$ of these locations is below the household's disposable income. If the current location becomes too expensive for the household, it is no longer within the budget set, and the household is forced to move (displacement).

$$ B_i(t) = \{x \in X(t): (\ L(x, t) = \{\emptyset\} \ \lor \ L(x, t) = \{i\}) \ \land \ p(x, t) \leq w_i \} $$

Suppose households choose their housing unit according to the discussed preferences. In that case, their choice of housing unit $x$ can be treated *as if* they maximize their utility under the constraint that they need to be able to afford this location:

$$ \operatorname*{arg\,max}_{x \in B_i(t)} U(x, t) \\* $$

If no housing units are available with rent below or equal to the household's disposable income, the household moves to the empty location with the lowest rent.

In [8]:
class Household(ap.Agent):

    def setup(self):
        """ Household agents are initiated with random income and status. """
        r_correlation = self.model.p.r_correlation
        distribution = self.model.p.distribution
        # fixed attributes
        self.income = np.random.beta(a = distribution, b = 2.5 * distribution, size = 1)[0]
        self.status = (1 - r_correlation) * np.random.beta(a = distribution, b = 2.5 * distribution, size = 1)[0] + r_correlation * self.income

    def moving(self):
        """ Households move to the housing unit that maximises their residential satisfaction given their income.
        If households cannot afford any available housing units, they move to the unit with cheapest rent. """
        available_positions = set(self.model.household_grid.empty)
        available_positions.add(self.model.household_grid.positions[self])
        # Filter the available choice set (Landlords in available positions)
        choice_set = [
            landlord for landlord, pos in self.model.landlord_grid.positions.items()
            if pos in available_positions
        ]
        # Filter choice set by affordability (budget set)
        budget_set = [landlord for landlord in choice_set if landlord.rent <= self.income]
        if budget_set:  # If there are options within the budget
            # Find the housing unit with the maximum utility within the budget
            max_utility = max(budget_set, key=lambda landlord: landlord.utility)
            housing_unit = self.model.landlord_grid.positions[max_utility]
        else:  # No affordable options, select the cheapest rent
            min_rent = min(choice_set, key=lambda landlord: landlord.rent)
            housing_unit = self.model.landlord_grid.positions[min_rent]
        # Move to the selected housing unit
        self.model.household_grid.move_to(self, housing_unit)

### Landlords

Landlords supply housing quality $q(x, t)$ of housing unit $x$. $q(x, t)$ represents the monetary value of housing quality independent of the neighborhood. Quality is path-dependent; it is dependent on past investments. Landlords invest in their housing quality if the average rent in the Moore neighborhood increases. As landlords would like to know whether investing will be profitable, an increase in average neighborhood rent indicates that their neighborhood attracts wealthy residents who are able to provide a return on investment. However, if the rents in the neighborhood decrease, returns in this neighborhood are too low to justify investments.

As $q(x, t)$ represents the monetary value of housing quality, landlords set housing quality equal to the average neighborhood rent if they invest. This also reflects that landlords are responsive to the size of the change in neighborhood incomes. If neighborhood incomes only rise slightly, they will not invest large sums of money. If they do not invest, housing quality decays exponentially. The decay parameter $d \in [0, 1[$ gives the proportion of housing quality a unit retains after one time step without investment.

If $x_j$ is one of the eight housing units in the Moore neighborhood of housing unit $x_i$ at time $t$, the average rent $\bar{p}(x_i, t)$ in the neighborhood of $x_i$ at time $t$ is given by:

$$ \bar{p}(x_i, t) = \frac{1}{8} \sum_{k = 1}^{8} p(x_j, t) $$

$$
q(x_i, t) = 	\begin{cases}
			\bar{p}(x_i, t) & \bar{p}(x_i, t) \geq \bar{p}(x_i, t-1) \\
			d * q(x_i, t-1) & \bar{p}(x_i, t) < \bar{p}(x_i, t-1)
			\end{cases}
$$

In [9]:
class Landlord(ap.Agent):

    def setup(self):
        """ Landlord agents are initiated with initially random housing quality.
        Utility and rents are equal to the housing quality at setup.
        Various variables are initiated that are filled at model setup or updated throughout the simulation."""
        distribution = self.model.p.distribution
        self.housing_quality = np.random.beta(a = distribution, b = 2.5 * distribution, size = 1)[0]
        self.utility = self.housing_quality
        self.rent = self.housing_quality
        self.pos = None # filled at model setup
        self.x_coord = None
        self.y_coord = None
        self.nb_pos = []
        self.nb_landlords = []
        self.hh_id = None # updated throughout simulation based on household occupying the unit
        self.hh_income = None
        self.hh_status = None

    def update_quality_and_utility(self):
        """ If neighborhood average rent rises, landlords invest in their housing quality. If not, it decays.
        Utility is calculated based on the housing quality and the status of the households in the neighborhood."""
        a_preferences = self.model.p.a_preferences
        d_decay = self.model.p.d_decay
        households_nb = (household for household, position in self.model.household_grid.positions.items() if position in self.nb_pos)

        mean_rent = np.mean([landlord.rent for landlord in self.nb_landlords])
        if self.housing_quality <= mean_rent:
            self.housing_quality = mean_rent
        else:
            self.housing_quality *= d_decay

        household_status_values = [household.status for household in households_nb]
        if household_status_values:
            mean_status = np.mean(household_status_values)
            self.utility = (mean_status ** a_preferences) * (self.housing_quality ** (1 - a_preferences))
        else:
            self.utility = 0

    def reporting(self):
        """ I only export data from the landlords.
        To also have access to the household data,
        I get the household id, income, and status from the household agent that occupies the landlord's unit."""
        my_renter = next( # as there is only one, the iteration can stop when a match has been found
            (household for household, pos in self.model.household_grid.positions.items() if pos == self.pos),
            None
        )
        if my_renter is None:
            self.hh_id = None
            self.hh_income = None
            self.hh_status = None
        else:
            self.hh_id = my_renter.id
            self.hh_income = my_renter.income
            self.hh_status = my_renter.status

    def update_rent(self): # for substantive description, see next section.
        """ Rents are calculated based on the city-wide distribution of utility and income."""
        competition = self.model.utility_income_df[
            (self.model.utility_income_df['utility'] <= self.utility) &
            self.model.utility_income_df['hh_income'].notna()
            ]['hh_income']
        if competition.empty:
            self.rent = self.model.utility_income_df['hh_income'].min()
        else:
            self.rent = np.percentile(competition, 75)

## Rent

The price or rent the household pays the landlord to live at a given housing unit is a result of supply and demand in competitive markets. Specifically, rent is a mapping of desirability of the housing unit onto the income distribution. The housing units providing the highest residential satisfaction will have the fiercest competition between interested renters, and the renters with the highest disposable income can outprice the others. Therefore, the units with the highest residential satisfaction will be the most expensive, while the least expensive have the lowest level of residential satisfaction. To implement such a price-building mechanism, I decided to model rent as the 75th percentile of the incomes of all renters living in a housing unit with a lower residential satisfaction than their unit provides. Renters living in housing units with lower residential satisfaction want to move there because they can increase their residential satisfaction by moving to this housing unit. The renters in better housing units have no incentive to move to this unit. The 75th percentile is somewhat arbitrary but gives some leeway for movements to occur, whereas asking the maximum income of renters in a lower utility housing unit as rent makes it very unlikely that a household will move there. The lower rent than potentially achievable reduces the time the landlord needs to wait until a renter willing to pay the asking price moves in.

$C(x_i, t)$ denotes all housing units $x_j$ that have a lower utility than $x_i$, which are the competition of $x_i$. Rent is then the 75th percentile of incomes of the households $L(C_i)$ living in the housing units in the competition set.

$$ C(x_i, t) = \{ x \in X: U(x_j, t) \leq U(x_i, t)  \} $$

$$ p(x, t) = P_{75}[\{ L(C_i): w_i  \}] $$

In [10]:
## Create a dataframe of all incomes and utilities for rent calculations of households
def utility_income_data(model):
    """ Create a dataframe of all incomes and utilities for rent calculations of landlords. """
    utility_income_df = pd.DataFrame(
        [(landlord.utility, landlord.hh_income) for landlord in model.landlords],
        columns=['utility', 'hh_income']
    )
    return utility_income_df

## Model Setup and Scheduling

The two classes of agents interact on a spatial grid that represents a city. The *size* parameter sets the edge length of the square grid. Each cell of the grid represents one housing unit into which a household can move and a landlord can invest. The number of housing units (and consequently landlords) is *size* squared. To avoid edge effects, the edges of the grid loop around to create a torus.  The *density* $\in ]0, 1[$ parameter sets the population density by setting the number of households to *density* * *size* ** 2. Consequently, a proportion of 1 - *density* of the housing units are vacant at every point in time. At setup, exactly one landlord class agent is placed on every grid cell while the household class agents are distributed randomly on the still empty cells. At every point in time, only one household class agent can occupy a single cell.

At every time step after the setup, all landlords first update their respective variables and decide to invest or not. Then, all households decide whether and where to move. After moving (or staying), the households update their respective variables.

If the parameter *turnover* ($\in [0, 0.1]$) is greater 0, a corresponding proportion of all households are removed from the grid and newly created households are added to empty housing units. This represents population dynamics, where people move in and out of the city. This creates random moves which introduce noise. Noise has been shown to affect results of computational models, often improving their empirical fit (Macy and Tsvetkova 2015, Mäs and Helbing 2020). It also ensures that agents move to their optimal location and not get stuck in suboptimal equilibria. The latter can be achieved with high vacancy rates or population turnover (Fossett and Waren 2005).

There is no natural end to this simulation. After a burn-in period, spatial patterns emerge. The time the model is run and the time disgarded for analysis as the burn-in are set arbitrarily in the computational experiments based on visual inspection.

In [11]:
class SocEconHousing(ap.Model):

    def setup(self):
        size = self.p.size
        density = self.p.density
        vision = self.p.vision
        n_housing_units = size ** 2
        n_households = int(density * n_housing_units)

        # Create Household grid and Household class agents and distribute them randomly on empty cells.
        self.household_grid = ap.Grid(self,
                                      shape = (size, size),
                                      torus = True,
                                      track_empty = True)
        self.households = ap.AgentList(self, n_households, Household)
        self.household_grid.add_agents(self.households,
                                       random = True,
                                       empty = True)
        for household in self.household_grid.agents:
            household.pos = self.household_grid.positions[household]
            household.x_coord, household.y_coord = household.pos

        # Create Landlord grid and Landlord class agents and add exactly one to every cell.
        self.landlord_grid = ap.Grid(self,
                                     shape = (size, size),
                                     torus = True,
                                     track_empty = True)
        self.landlords = ap.AgentList(self, n_housing_units, Landlord)
        self.landlord_grid.add_agents(self.landlords,
                                      random = True,
                                      empty = True)
        for landlord in self.landlord_grid.agents:
            landlord.pos = self.landlord_grid.positions[landlord]
            landlord.x_coord, landlord.y_coord = landlord.pos
            landlord.nb_landlords = self.model.landlord_grid.neighbors(landlord, distance = vision).to_list()  # list of Landlord class agents on neighboring positions
            landlord.nb_pos = [self.model.landlord_grid.positions[landlord] for landlord in landlord.nb_landlords]  # list of position tuples of the neighborhood

        self.utility_income_df = utility_income_data(self)


    def step(self):
        """ Step function for the model. First, the landlords decide whether to invest into their housing quality,
        then they set their rents, and finally the households move to the housing unit with the highest utility.
        If there is turnover, households are removed and new ones are added."""
        self.landlords.update_quality_and_utility()
        self.utility_income_df = utility_income_data(self)
        self.landlords.update_rent()
        self.landlords.reporting()

        self.household_grid.agents.moving()

        # population dynamics
        if self.model.p.turnover > 0:
            turnover = self.p.turnover
            n_households = int(self.p.density * self.p.size * self.p.size)
            pop_change = int(turnover * n_households)

            outmovers = random.sample(list(self.household_grid.agents), pop_change)
            self.household_grid.remove_agents(outmovers)

            inmovers = ap.AgentList(self, pop_change, Household)
            self.household_grid.add_agents(inmovers, random = True, empty = True)
            for household in inmovers:
                household.pos = self.household_grid.positions[household]
                household.x_coord, household.y_coord = household.pos

    def update(self):
        """ Update function for the model. I only export data from the landlords."""
        self.landlords.record(['id', 'x_coord', 'y_coord', 'housing_quality', 'utility', 'rent', 'hh_id', 'hh_income', 'hh_status'])

## Single-run Animation

The following animation shows how spatial patterns in income, status, housing quality and rents emerge in this model. The parameters chosen for this single animation are chosen to reflect the empirically most plausible conditions: households value housing quality more than neighborhood status and household income and status is highly but not perfectly correlated.

In [12]:
parameters = {
    'r_correlation': 0.7, # correlation between income and status
    'a_preferences': 0.3, # To which extent is the price determined by neighbors' income
    'distribution': 2, # number between 1 and 5, determines the shape of the Beta dist
    'd_decay': 0.95, # how much housing quality is retained in one time step if landlords do not invest
    'density': 0.85, # Density of population
    'size': 20, # Height and length of the grid TODO 30
    'vision': 1, # distance from the unit the agents consider as neighbors
    'turnover': 0.02, # population dynamics: proportion of households that move in and out of the city
    'steps': 100  # Maximum number of steps
    }

def animation_plot(model, axs):
    [ax_inc, ax_sta, ax_hq, ax_rt] = axs
    fig.suptitle(f"Residential Segregation / Spatial Inequalities by Attribute \n Time-step: {model.t}")
    income_grid = model.household_grid.attr_grid('income')
    ap.gridplot(income_grid, cmap='viridis', ax=ax_inc)
    ax_inc.set_title("Income")
    status_grid = model.household_grid.attr_grid('status')
    ap.gridplot(status_grid, cmap='viridis', ax=ax_sta)
    ax_sta.set_title("Status")
    quality_grid = model.landlord_grid.attr_grid('housing_quality')
    ap.gridplot(quality_grid, cmap='viridis', ax=ax_hq)
    ax_hq.set_title("Housing Quality")
    rent_grid = model.landlord_grid.attr_grid('rent')
    ap.gridplot(rent_grid, cmap='viridis', ax=ax_rt)
    ax_rt.set_title("Rent")

fig, axs = plt.subplots(nrows = 1, ncols = 4)
model = SocEconHousing(parameters)
animation = ap.animate(model, fig, axs, animation_plot)
IPython.display.HTML(animation.to_jshtml())

## Computational Experiments

The following sections describe the computational experiments I have conducted with this model. The experiments are computationally expensive. I have conducted these experiments as separate Python files on the Helix and bwCluster3.0 high performance computing clusters, funded by the German federal state of Baden-Württemberg.

### Main Experiment

This section describes the setup of the simulation experiment for the main article. This main experiment simulates a 30x30 "city" (grid) with 85% of all units being occupied. Therefore, there are 900 housing units and 765 households in each simulation. Income is distributed with a Beta(2, 5) distribution and 2 percent of all households are removed at each time step and the same number is added to model population dynamics. Households calculate utility and landlords make their investment decisions based on the Moore neighborhood with a distance of one, so the 8 neighboring cells. The parameters to vary are the correlation between income and status, as well as the relative importance of housing quality versus neighbors in households' preferences. Both of these parameters vary from 0 to 1 in steps of 0.25, so have 5 levels. I also vary the decay parameter between 0.95, 0.9, 0.85 and 0.8. Each parameter combination is run 15 times, resulting in 5 x 5 x 4 x 15 = 1500 runs. Each run lasts 400 steps but only the last 100 steps are saved for analysis.

The data are prepared and saved for analysis (see separate files) and reuse by other researchers. As the data record variables from every household and housing unit at every time step, I record 900 housing units x 1500 runs x 400 time steps = 540 million observations for housing units of which 135 million are analysed.

### Robustness Check 1: Population Dynamics and Noise

Computational models that converge to an equilibrium might get stuck in a local equilibrium and some equilibria might not be stable. It has been shown that adding noise to computational experiments results in different, often better, predictions for real systems (Macy and Tsvetkova 2015, Mäs and Helbing 2020). An intuitive way to think about random events in residential mobility are moves into and out of the city. The parameter turnover sets which proportion of households move out and into the city at every time step, so that the population density stays constant.

The model simulates a grid of 30x30 and uses 3 x 3 x 2 = 18 levels of the initial parameters and additionally 4 levels of turnover, 0, 0.02, 0.05 and 0.1. The model repeats every combination 10 times, so the experiment consists of 18 x 4 x 10 = 720 runs. Visual analysis suggests that the model converges to the equilibrium before 100 steps with this size. Therefore, the model runs 200 steps. The output results in 30 x 30 x 720 x 200 = 129.6 million observations of housing units of which 64.8 million are analysed.

### Robustness Check 2: Income Inequality

It has been an established that increases in income inequality cause increases in income segregation (e.g., Reardon and Bischoff 2011, Yavas 2019). This experiment calculates a reduced model that additionally varies the income and status distribution. The Beta distribution in the model is set up to always be unimodal and right skewed with an expected value of about 0.2857: Beta(a = distribution, b = 2.5 * distribution). The distribution parameter therefore varies only income inequality but not average income.

The model simulates a grid of 30x30 and uses 3 x 3 x 2 = 18 levels of the initial parameters and additionally 3 levels of inequality. Specifically, I use income distributions of Beta(1, 2.5), Beta(2, 5) and Beta(3, 7.5). These distributions correspond to Gini indices of about 0.42, 0.32, and 0.26 respectively. The model repeats every combination 10 times, so the experiment consists of 18 x 3 x 10 = 540 runs of 200 steps. The output results in 30 x 30 x 540 x 200 = 97.2 million observations of housing units of which 48.6 million are analysed.

### Robustness Check 3: Vision / Size of Neighborhoods

In their paper, Laurie and Jaggi (2003) have established that in categorical segregation models, it makes a difference what agents consider their neighborhood. Before, I have used a Moore neighborhood of distance 1, which refers to the 8 bordering (including diagonally) cells. Using the vision parameter, I can increase this distance. I vary it between 1 (8 neighbors), 2 (24 neighbors) and 3 (48 neighbors).

The model simulates a grid of 30x30 and uses 3 x 3 x 2 = 18 levels of the initial parameters and additionally 3 levels of vision. The model repeats every combination 10 times, so the experiment consists of 18 x 3 x 10 = 540 runs of 200 steps. The output results in 30 x 30 x 540 x 200 = 97.2 million observations of housing units of which 48.6 million are analysed.

### Robustness Check 4: NetLogo Model

To limit the possibility of coding errors in the ABM and the analysis and to give researchers more opportunities to replicate the results, I also have written the ABM in NetLogo and analyse its results in R (see separate files). This check also varies the definition of a neighborhood in the calculation of segregation measures between 4x4 and 8x8 neighborhoods.

### Data Set for Hypothesis Generation

The main experiment and the robustness checks use global parameters that span the entire range possible. However, some values of these parameters are very unlikely to be realised in the real world. I therefore simulate a data set for hypothesis generation that only slightly varies the global parameters around realistic values. As households tend to value housing quality to a greater extent than neighbourhood quality, I use values of 0.2, 0.3 and 0.4 for the relative importance parameter $a$ in the utility function. Income and status also tend to be highly correlated, although not perfectly. I use correlation parameter values of 0.5, 0.6 and 0.7 (the correlation parameter tends to produce Pearson correlations between the two variables higher than the parameter value). And housing quality decays slowly over time, so I use decay parameter values of 0.95, 0.925 and 0.9.

This selection of parameter values results in 27 combinations and each combination is run ten times, resulting in 270 independent simulation runs of 200 steps. With a grid size of 30 x 30, the raw output data amounts to 48.6 million observations of housing units and 24.3 million of these are analysed.

## References

Benard, Stephen, and Robb Willer. 2007. “A Wealth and Status-Based Model of Residential Segregation.” Journal of Mathematical Sociology 31(2):149–74. doi: 10.1080/00222500601188486.

Fossett, Mark, and Warren Waren. 2005. “Overlooked Implications of Ethnic Preferences for Residential Segregation in Agent-Based Models.” Urban Studies 42(11):1893–1917. doi: 10.1080/00420980500280354.

Laurie, Alexander J., and Narendra K. Jaggi. 2003. “Role of ‘Vision’ in Neighbourhood Racial Segregation: A Variant of the Schelling Segregation Model.” Urban Studies 40(13):2687–2704. doi: 10.1080/0042098032000146849.

Macy, Michael, and Milena Tsvetkova. 2015. “The Signal Importance of Noise.” Sociological Methods & Research 44(2):306–28. doi: 10.1177/0049124113508093.

Mäs, Michael, and Dirk Helbing. 2020. “Random Deviations Improve Micro–Macro Predictions: An Empirical Test.” Sociological Methods & Research 49(2):387–417. doi: 10.1177/0049124117729708.

Reardon, Sean F., and Kendra Bischoff. 2011. “Income Inequality and Income Segregation.” American Journal of Sociology 116(4):1092–1153. doi: 10.1086/657114.

Schelling, Thomas C. 1971. “Dynamic Models of Segregation.” Journal of Mathematical Sociology 1:143–86.

Yavaş, Mustafa. 2019. “Dissecting Income Segregation: Impacts of Concentrated Affluence on Segregation of Poverty.” Journal of Mathematical Sociology 43(1):1–22. doi: 10.1080/0022250X.2018.1476858.